In [34]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, NumeralTickFormatter
from bokeh.transform import factor_cmap
from bokeh.palettes import Category10
from bokeh.io import output_notebook
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [35]:
df = pd.read_csv('data_clean.csv')

In [36]:
df

id       node_id                                      full_name  \
0      443592401  R_kgDOGnCu0Q                               progfolio/elpaca   
1      443476254  R_kgDOGm7pHg                         MoserMichael/pyasmtool   
2      443522708  R_kgDOGm-elA                victoryhb/streamlit-option-menu   
3      443522851  R_kgDOGm-fIw                                yihong0618/2022   
4      443529166  R_kgDOGm-3zg                        ice-doom/codeql_compile   
...          ...           ...                                            ...   
12890  654902184  R_kgDOJwkDqA                      ConnectAI-E/Go-Midjourney   
12891  654899923  R_kgDOJwj60w                    Implex-ltd/Implex-generator   
12892  654827428  R_kgDOJwffpA  supershaneski/openai-api-function-call-sample   
12893  655021349  R_kgDOJwrVJQ                             itrewm/Snapp-prize   
12894  654989401  R_kgDOJwpYWQ               zodiacon/winnativeapibooksamples   

                                             description  \
0                               an elisp package manager   
1      explores the python bytecode provides some too...   
2      streamlitoptionmenu is a simple streamlit comp...   
3                                            2022 gogogo   
4      automatically decompile closed-source applicat...   
...                                                  ...   
12890  invoking midjourney's drawing ability in the f...   
12891                     implex discord token generator   
12892  a sample nextjs app to demonstrate the newly a...   
12893  by using this project you can automatically co...   
12894  samples from my book windows native api progra...   

                      created_at                 updated_at  \
0      2022-01-01 17:49:54+00:00  2023-06-29 19:18:19+00:00   
1      2022-01-01 05:20:02+00:00  2023-06-15 15:04:13+00:00   
2      2022-01-01 11:13:17+00:00  2023-06-28 17:38:15+00:00   
3      2022-01-01 11:14:17+00:00  2023-06-27 05:23:04+00:00   
4      2022-01-01 11:56:33+00:00  2023-06-14 03:27:18+00:00   
...                          ...                        ...   
12890  2023-06-17 09:28:56+00:00  2023-07-04 03:59:02+00:00   
12891  2023-06-17 09:20:53+00:00  2023-07-03 11:41:13+00:00   
12892  2023-06-17 04:21:43+00:00  2023-07-06 06:25:28+00:00   
12893  2023-06-17 16:29:08+00:00  2023-06-28 12:48:14+00:00   
12894  2023-06-17 14:40:03+00:00  2023-07-05 15:40:37+00:00   

                       pushed_at   size  has_issues  has_projects  ...  \
0      2023-06-27 21:16:39+00:00   1366        True          True  ...   
1      2023-02-16 08:48:51+00:00    111        True          True  ...   
2      2023-05-30 14:39:32+00:00    159        True          True  ...   
3      2023-04-12 07:29:07+00:00   1031        True          True  ...   
4      2022-03-02 10:52:10+00:00     19        True          True  ...   
...                          ...    ...         ...           ...  ...   
12890  2023-06-26 03:54:28+00:00     45        True          True  ...   
12891  2023-06-28 22:03:17+00:00  22406        True          True  ...   
12892  2023-06-30 04:15:47+00:00    770        True          True  ...   
12893  2023-06-26 00:12:01+00:00     17        True          True  ...   
12894  2023-07-04 01:44:19+00:00    137        True          True  ...   

       watchers                                      language_name  \
0             9  ['Emacs Lisp', 'Makefile', 'Dockerfile', 'Shell']   
1             6                    ['Python', 'Shell', 'Makefile']   
2             6  ['Vue', 'Python', 'TypeScript', 'JavaScript', ...   
3            12                        ['Python', 'Rust', 'Shell']   
4             4                                         ['Python']   
...         ...                                                ...   
12890         7                               ['Go', 'Dockerfile']   
12891         0         ['Go', 'JavaScript', 'Python', 'Makefile']   
12892         3                             

### repo

In [37]:
df['created_at'] = pd.to_datetime(df['created_at'])
df['updated_at'] = pd.to_datetime(df['updated_at'])
df['pushed_at'] = pd.to_datetime(df['pushed_at'])

In [38]:
df['month'] = df['created_at'].dt.month
projects_by_month = df.groupby('month')['id'].count()

In [43]:
# Création d'un DataFrame avec le nombre de projets créés par mois
df_projects_by_month = projects_by_month.reset_index()
df_projects_by_month.columns = ['Month', 'Number of Projects Created']

# Création du graphique en ligne à l'aide de Plotly
fig = px.line(df_projects_by_month, x='Month', y='Number of Projects Created', markers=True)

# Personnalisation de la mise en page du graphique
fig.update_layout(
    title='Tendances de la création de projets par mois',
    xaxis_title='Mois',
    yaxis_title='Number of Projects Created',
    xaxis={'type': 'category'},
    yaxis={'gridcolor': 'lightgray'},
    hovermode='x',
    legend={'orientation': 'h', 'y': -0.2},)

fig.show()

In [44]:
# Créer un DataFrame avec la taille moyenne des projets par mois
avg_size_by_month = df.groupby('month')['size'].mean()
df_avg_size_by_month = avg_size_by_month.reset_index()
df_avg_size_by_month.columns = ['Month', 'Average Project Size']

# Créer le graphique en ligne en utilisant Plotly
fig = px.line(df_avg_size_by_month, x='Month', y='Average Project Size', markers=True)

# Personnaliser la mise en page du graphique
fig.update_layout(
    title='Tendances de la taille moyenne des projets par mois',
    xaxis_title='Mois',
    yaxis_title='Taille moyenne du projet',
    xaxis={'type': 'category'},
    yaxis={'gridcolor': 'lightgray'},
    hovermode='x',
    legend={'orientation': 'h', 'y': -0.2},)
fig.show()

In [8]:
projects_updated_by_month = df.groupby('month')['updated_at'].count()
projects_pushed_by_month = df.groupby('month')['pushed_at'].count()

# Create a figure object
fig = go.Figure()

# Add the line trace for project updates
fig.add_trace(go.Scatter(
    x=projects_updated_by_month.index,
    y=projects_updated_by_month.values,
    name='Projects Updated',
    mode='lines',
    line=dict(color='blue')
))

# Add the line trace for project pushes
fig.add_trace(go.Scatter(
    x=projects_pushed_by_month.index,
    y=projects_pushed_by_month.values,
    name='Projects Pushed',
    mode='lines',
    line=dict(color='green')
))

# Customize the chart layout
fig.update_layout(
    title='Trends in Project Updates and Pushes by Month',
    xaxis_title='Month',
    yaxis_title='Number of Projects',
    xaxis={'type': 'category'},
    yaxis={'gridcolor': 'lightgray'},
    hovermode='x',
    legend={'orientation': 'h', 'y': -0.2},
)

# Show the chart
fig.show()


In [47]:
# Extraire l'année et le mois de la colonne 'created_at'
df['year_month'] = df['created_at'].dt.to_period('M')

# Regrouper les données par année et mois et calculer le nombre médian d'étoiles (stars), de forks et de watchers
median_stars_by_month = df.groupby('year_month')['star'].median()
median_forks_by_month = df.groupby('year_month')['forks'].median()
median_watchers_by_month = df.groupby('year_month')['watchers'].median()

# Configurer la figure
output_notebook()
p = figure(x_range=median_stars_by_month.index.astype(str).tolist(), plot_width=800, plot_height=400,
           title='Popularité des projets au fil du temps', x_axis_label='Année-Mois', y_axis_label='Nombre médian')

# Tracer le nombre médian d'étoiles, de forks et de watchers au fil du temps
p.line(median_stars_by_month.index.astype(str).tolist(), median_stars_by_month.values, legend_label='Étoiles', line_color='blue')
p.line(median_forks_by_month.index.astype(str).tolist(), median_forks_by_month.values, legend_label='Forks', line_color='green')
p.line(median_watchers_by_month.index.astype(str).tolist(), median_watchers_by_month.values, legend_label='Watchers', line_color='red')

# Formater les étiquettes des ticks de l'axe y en nombres entiers
p.yaxis.formatter = NumeralTickFormatter(format="0")

# Faire pivoter les étiquettes des ticks de l'axe x
p.xaxis.major_label_orientation = 45

# Afficher le graphique
show(p)


C:\Users\amine\AppData\Local\Temp\ipykernel_3360\2340791751.py:5: UserWarning:

Converting to PeriodArray/Index representation will drop timezone information.



Loading BokehJS ...

In [56]:
# Get the current date with the appropriate timezone
current_date = datetime.now(pytz.utc)

# Calculate the age of open issues
df['issue_age'] = (current_date - df['created_at']).dt.days

# Analyze frequency of updates
df['update_frequency'] = (df['updated_at'] - df['created_at']).dt.days

# Analyze activity by pushes
df['push_activity'] = (df['updated_at'] - df['pushed_at']).dt.days

# Print the analysis results
print("Age of Open Issues:")
print(df['issue_age'].describe().round(2))
print()

print("Frequency of Updates:")
print(df['update_frequency'].describe().round(2))
print()

print("Activity by Pushes:")
print(df['push_activity'].describe().round(2))


Age of Open Issues:
count    12895.00
mean       278.59
std        172.07
min         23.00
25%        123.00
50%        250.00
75%        434.00
max        556.00
Name: issue_age, dtype: float64

Frequency of Updates:
count    12895.00
mean       255.78
std        166.62
min          0.00
25%        108.00
50%        231.00
75%        410.00
max        545.00
Name: update_frequency, dtype: float64

Activity by Pushes:
count    12895.00
mean        93.31
std        123.22
min       -218.00
25%          6.00
50%         42.00
75%        132.00
max        539.00
Name: push_activity, dtype: float64


In [57]:
print(df[['full_name', 'contributors']])

                                           full_name  \
0                                   progfolio/elpaca   
1                             MoserMichael/pyasmtool   
2                    victoryhb/streamlit-option-menu   
3                                    yihong0618/2022   
4                            ice-doom/codeql_compile   
...                                              ...   
12890                      ConnectAI-E/Go-Midjourney   
12891                    Implex-ltd/Implex-generator   
12892  supershaneski/openai-api-function-call-sample   
12893                             itrewm/Snapp-prize   
12894               zodiacon/winnativeapibooksamples   

                                            contributors  
0      [{'login': 'progfolio', 'id': 44036031, 'node_...  
1      [{'login': 'MoserMichael', 'id': 812100, 'node...  
2      [{'login': 'victoryhb', 'id': 3033215, 'node_i...  
3      [{'login': 'yihong0618', 'id': 15976103, 'node...  
4      [{'login': 'ice-doom', 'i

In [58]:
contrib_df = df[['full_name', 'top_10_contributors']].explode('top_10_contributors')
top_contrib_df = contrib_df.groupby('full_name').count().sort_values(by='top_10_contributors', ascending=False).head(20)
top_contrib_repos = top_contrib_df.index.tolist()

In [59]:
import ast

# Convert string representations of dictionaries to actual dictionaries
df['contributors'] = df['contributors'].apply(ast.literal_eval)

# Calculate the total contributions for each repository
df['Total Contributions'] = df['contributors'].apply(lambda x: sum([contrib['contributions'] for contrib in x]))

# Sort the DataFrame based on total contributions in descending order
df_sorted_by_contributions = df.sort_values('Total Contributions', ascending=False)

# Select the top 20 repositories
top_20_repos = df_sorted_by_contributions.head(20)

# Print the top 20 repositories
print("Top 20 Repositories based on Total Contributions:")
print(top_20_repos[['full_name', 'Total Contributions']])


Top 20 Repositories based on Total Contributions:
                                    full_name  Total Contributions
5490                    arielherself/espresso                12144
694                    proxmox/proxmox-backup                 6696
10220                     vfarid/cf-clean-ips                 6624
7362     7oSkaaa/LeetCode_DailyChallenge_2023                 6090
7627                     cuixiaorui/VSCodeVim                 5867
7775                         buroa/k8s-gitops                 5265
2747                        szinn/k8s-homelab                 4188
2410   perpetual-protocol/perp-curie-contract                 3327
305                     NickvisionApps/Denaro                 3065
3639                         Gh0stBlade/KAIN2                 2929
5742                       codinasion/program                 2732
7958                    gngpp/Actions-OpenWrt                 2722
3466        matterandvoid-space/subscriptions                 2628
6874        

In [60]:
# Création d'un graphique à barres
fig = go.Figure(data=go.Bar(
    x=top_20_repos['Total Contributions'],
    y=top_20_repos['full_name'],
    orientation='h',
    marker_color='blue'
))

# Personnalisation de la mise en page
fig.update_layout(
    title='Top 20 des dépôts basés sur les contributions totales',
    xaxis_title='Contributions totales',
    yaxis_title='Dépôt',
    yaxis_autorange='reversed'
)

fig.show()


#### statistiques descriptives

In [61]:
selected_columns = ['size', 'open_issues', 'star', 'watchers', 'forks']
stats = df[selected_columns].describe().round(2)
stats

size  open_issues      star  watchers     forks
count  12895.00     12895.00  12895.00  12895.00  12895.00
mean    3125.69         2.45     90.80      3.98     15.51
std     5222.59         3.30     66.74      2.76     49.07
min        0.00         0.00     10.00      0.00      0.00
25%      131.00         0.00     46.00      2.00      3.00
50%      679.00         1.00     68.00      3.00      7.00
75%     3430.00         4.00    115.00      5.00     16.00
max    25641.00        15.00    349.00     14.00   2636.00

### size

In [63]:
# Analyse de distribution - Histogramme
fig = px.histogram(df, x='size', nbins=20, color_discrete_sequence=['#008080'])
fig.update_layout(
    xaxis_title='Taille',
    yaxis_title='Fréquence',
    title='Distribution des tailles de projet',
    plot_bgcolor='white',
    paper_bgcolor='white'
)
fig.show()

# Analyse de séries temporelles - Graphique linéaire
df['created_at'] = pd.to_datetime(df['created_at'])  # Convert to datetime if necessary
df_sorted = df.sort_values('created_at')  # Sort by creation date
fig = px.line(df_sorted, x='created_at', y='size', color_discrete_sequence=['#800080'])
fig.update_layout(
    xaxis_title='Date',
    yaxis_title='Taille',
    title='Évolution des tailles de projet au fil du temps',
    plot_bgcolor='white',
    paper_bgcolor='white'
)
fig.show()


In [66]:
# Définir les limites des intervalles et les étiquettes pour les catégories
bin_edges = [0, 500, 1000, 5000, float('inf')]
bin_labels = ['Petit', 'Moyen', 'Grand', 'Très grand']

# Créer une nouvelle colonne 'size_category' basée sur la colonne 'size'
df['size_category'] = pd.cut(df['size'], bins=bin_edges, labels=bin_labels, right=False)


In [67]:
# Compter le nombre d'occurrences de chaque catégorie dans la colonne 'size_category'
category_counts = df['size_category'].value_counts()

# Afficher le décompte des catégories
print(category_counts)


size_category
Petit         5836
Grand         3091
Très grand    2569
Moyen         1399
Name: count, dtype: int64


In [68]:
# Préparer les données
data = {
    'size_category': ['Small', 'Large', 'Very Large', 'Medium'],
    'count': [1900, 1181, 983, 536]
}

# Calculer le pourcentage pour chaque catégorie
total_count = sum(data['count'])
data['percentage'] = [count / total_count * 100 for count in data['count']]

# Créer un diagramme circulaire avec Plotly
fig = px.pie(data, values='count', names='size_category', 
             title='Catégories de taille des dépôts',
             labels={'count': 'Nombre', 'size_category': 'Catégorie de taille'},
             hover_data=['percentage'], 
             hover_name='size_category',
             hole=0.4)

# Définir le format du pourcentage pour l'étiquette au survol
fig.update_traces(textinfo='percent+label')

# Afficher le graphique
fig.show()


#### open_issues

In [69]:
# Créer l'histogramme de la distribution des open_issues
fig = px.histogram(df, x='open_issues', nbins=20)

# Personnaliser les titres des axes et le titre du graphique
fig.update_layout(
    xaxis_title='Open Issues',
    yaxis_title='Fréquence',
    title='Distribution des Open Issues'
)

# Afficher le graphique
fig.show()


In [71]:
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import NumeralTickFormatter

# Convertir la colonne "created_at" en datetime
df['created_at'] = pd.to_datetime(df['created_at'])

# Regrouper les données par date et compter le nombre de open_issues pour chaque date
trend_data = df.groupby(df['created_at'].dt.date)['open_issues'].count()

# Créer une figure Bokeh
output_notebook()  # Afficher le graphique dans Jupyter Notebook
p = figure(title='Analyse de tendance des Open Issues', x_axis_type='datetime', sizing_mode='stretch_both',
           background_fill_color='#f2f2f2', tools='hover')

# Tracer la ligne de tendance
p.line(trend_data.index, trend_data.values, line_width=2, color='#007bff', legend_label='Open Issues')
p.circle(trend_data.index, trend_data.values, size=6, color='#007bff', alpha=0.8, legend_label='Open Issues')

# Personnaliser le graphique
p.xaxis.axis_label = 'Date'
p.yaxis.axis_label = 'Nombre de Open Issues'
p.xaxis.formatter.days = '%m/%d/%Y'  # Formater les étiquettes de l'axe x
p.yaxis.formatter = NumeralTickFormatter(format='0')  # Formater les étiquettes de l'axe y en entiers
p.legend.location = 'top_left'
p.legend.label_text_font_size = '12px'

# Appliquer des aspects esthétiques supplémentaires
p.toolbar.logo = None
p.grid.grid_line_alpha = 0.3 
p.border_fill_color = '#ffffff' 

# Afficher le graphique
show(p)


Loading BokehJS ...

In [75]:
# Catégoriser les problèmes en fonction des mots-clés dans la description
for index, row in df.iterrows():
    description = row['description']
    if isinstance(description, str):
        description = description.lower()
    else:
        category = 'Non_classe'


In [76]:
# Définir les comptes de catégories et les couleurs correspondantes
category_counts = {
    'Question': 84,
    'Documentation': 78,
    'Feature Request': 66,
    'Bug': 43
}

category_colors = {
    'Question': 'lightblue',
    'Documentation': 'lightgreen',
    'Feature Request': 'lightyellow',
    'Bug': 'lightcoral'
}

# Créer un DataFrame à partir des comptes de catégories
df_counts = pd.DataFrame({'category': list(category_counts.keys()), 'count': list(category_counts.values())})

# Créer le graphique à barres
fig = go.Figure(data=[go.Bar(x=df_counts['category'], y=df_counts['count'], marker_color=[category_colors[cat] for cat in df_counts['category']])])

# Personnaliser la mise en page
fig.update_layout(
    title='Comptes des catégories de problèmes',
    xaxis_title='Catégorie',
    yaxis_title='Compte',
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    font_color='black'
)

# Afficher le graphique
fig.show()


#### watchers

In [77]:
# Analyse de la distribution - Histogramme des Watchers
fig_histogram = px.histogram(df, x='watchers', nbins=20)
fig_histogram.update_layout(
    xaxis_title='Nombre de Watchers',
    yaxis_title='Fréquence',
    title='Distribution des Watchers'
)
fig_histogram.show()

# Analyse de séries temporelles - Graphique en ligne des Watchers
df['created_at'] = pd.to_datetime(df['created_at'])  # Conversion en format datetime si nécessaire
df_sorted = df.sort_values('created_at')  # Trier par date de création
fig_line = px.line(df_sorted, x='created_at', y='watchers')
fig_line.update_layout(
    xaxis_title='Date',
    yaxis_title='Nombre de Watchers',
    title='Évolution des Watchers au fil du temps'
)
fig_line.show()


In [164]:
fig = px.scatter(df, x='star', y='watchers', title='Stars vs. Watchers')
fig.update_layout(xaxis_title='Star', yaxis_title='Watchers')
fig.show()


### corrélation

In [78]:
# Sélectionner les colonnes numériques pour l'analyse de corrélation
numerical_columns = ['size', 'open_issues', 'star', 'watchers', 'forks']
numerical_df = df[numerical_columns]

# Calculer la matrice de corrélation
correlation_matrix = numerical_df.corr()

# Afficher la matrice de corrélation
print(correlation_matrix)


                 size  open_issues      star  watchers     forks
size         1.000000     0.070241  0.045059  0.067689  0.019901
open_issues  0.070241     1.000000  0.211716  0.214791  0.056987
star         0.045059     0.211716  1.000000  0.380878  0.178616
watchers     0.067689     0.214791  0.380878  1.000000  0.109431
forks        0.019901     0.056987  0.178616  0.109431  1.000000


In [79]:
# Sélectionner les colonnes numériques pour l'analyse de corrélation
numerical_columns = ['size', 'open_issues', 'star', 'watchers', 'forks']
numerical_df = df[numerical_columns]

# Calculer la matrice de corrélation
correlation_matrix = numerical_df.corr()

# Créer une heatmap avec Plotly
fig = px.imshow(correlation_matrix,
                x=numerical_columns,
                y=numerical_columns,
                color_continuous_scale='RdBu',
                zmin=-1,
                zmax=1)

# Personnaliser la mise en page de la heatmap
fig.update_layout(
    title='Matrice de corrélation',
    xaxis=dict(title='Variables'),
    yaxis=dict(title='Variables'),
    width=600,
    height=500
)

# Afficher la heatmap
fig.show()


#### contributors

In [80]:
# Calculer les contributions totales pour chaque contributeur
df['Total Contributions'] = df['contributors'].apply(lambda x: sum(contributor['contributions'] for contributor in x))

# Grouper les contributeurs par niveaux d'activité
df['Activity Level'] = pd.cut(df['Total Contributions'], bins=[0, 10, 50, 100, 500, float('inf')],
                              labels=['Faible', 'Modéré', 'Élevé', 'Très élevé', 'Super élevé'])

# Compter le nombre de contributeurs dans chaque niveau d'activité
activity_counts = df['Activity Level'].value_counts().sort_index()

# Afficher les décomptes des niveaux d'activité des contributeurs
print("Niveaux d'activité des contributeurs :")
print(activity_counts)


Niveaux d'activité des contributeurs :
Activity Level
Faible         2935
Modéré         5001
Élevé          2082
Très élevé     2396
Super élevé     331
Name: count, dtype: int64


In [83]:
import plotly.express as px

# Préparer les données
data = {
    'size_category': ['Faible', 'Modéré', 'Élevé', 'Très élevé', 'Super élevé'],
    'count': [880, 1648, 802, 1050, 184]
}

# Calculer le pourcentage pour chaque catégorie de contributeur
total_count = sum(data['count'])
data['percentage'] = [count / total_count * 100 for count in data['count']]

# Créer un diagramme circulaire avec Plotly
fig = px.pie(data, values='count', names='size_category', 
             title='Contributeurs',
             labels={'count': 'Nombre', 'size_category': 'Catégorie de taille'},
             hover_data=['percentage'], 
             hover_name='size_category',
             hole=0.4)

# Définir le format du pourcentage pour l'étiquette au survol
fig.update_traces(textinfo='percent+label')

# Afficher le graphique
fig.show()


In [87]:
# Créer un dictionnaire vide pour stocker les contributions totales de chaque contributeur
contributor_totals = {}

# Parcourir les lignes du DataFrame
for index, row in df.iterrows():
    contributors = row['contributors']
    
    # Parcourir les contributeurs dans chaque ligne
    for contributor in contributors:
        login = contributor['login']
        contributions = contributor['contributions']
        
        # Vérifier si le contributeur est déjà dans le dictionnaire, sinon ajouter une nouvelle entrée
        if login not in contributor_totals:
            contributor_totals[login] = 0
        
        # Ajouter les contributions au total pour le contributeur
        contributor_totals[login] += contributions

# Trier les contributeurs en fonction des contributions totales par ordre décroissant
sorted_contributors = sorted(contributor_totals.items(), key=lambda x: x[1], reverse=True)

# Sélectionner les 10 premiers contributeurs
top_10_contributors = sorted_contributors[:10]

# Afficher les 10 premiers contributeurs et leurs contributions totales
print("Top 10 Contributeurs :")
for contributor in top_10_contributors:
    print(f"Contributeur : {contributor[0]}, Contributions totales : {contributor[1]}")


Top 10 Contributeurs :
Contributeur : dependabot[bot], Contributions totales : 15827
Contributeur : arielherself, Contributions totales : 12144
Contributeur : renovate[bot], Contributions totales : 11704
Contributeur : vfarid, Contributions totales : 6620
Contributeur : github-actions[bot], Contributions totales : 3719
Contributeur : 7oSkaaa, Contributions totales : 3599
Contributeur : maurerdietmar, Contributions totales : 2974
Contributeur : Gh0stBlade, Contributions totales : 2754
Contributeur : repo-jeeves[bot], Contributions totales : 2660
Contributeur : actions-user, Contributions totales : 2544


In [88]:
# Obtenir les 10 principaux contributeurs et leurs contributions totales
top_10_contributors = sorted_contributors[:10]
contributors = [contributor[0] for contributor in top_10_contributors]
contributions = [contributor[1] for contributor in top_10_contributors]

# Créer une ColumnDataSource avec les données
data = {
    'contributors': contributors,
    'contributions': contributions,
    'color': Category10[10]  # Palette de couleurs pour les barres
}
source = ColumnDataSource(data=data)

# Créer la figure
p = figure(x_range=contributors, plot_height=400, title="Top 10 contributeurs",
           toolbar_location=None, tools="")

# Ajouter les barres au graphique
p.vbar(x='contributors', top='contributions', width=0.9, color='color', legend_field='contributors',
       source=source)

# Configurer le graphique
p.xgrid.grid_line_color = None
p.y_range.start = 0
p.xaxis.major_label_orientation = 1.2

# Afficher le graphique
show(p)


### langues

In [18]:
language_names = df['language_name']
language_percentages = df['language_percent']


In [19]:
language_frequencies = {}

for names, percentages in zip(language_names, language_percentages):
    for name, percentage in zip(names, percentages):
        if name in language_frequencies:
            language_frequencies[name] += percentage
        else:
            language_frequencies[name] = percentage


In [20]:
sorted_languages = sorted(language_frequencies.items(), key=lambda x: x[1], reverse=True)

In [21]:
df['language_name'] = df['language_name'].apply(ast.literal_eval)

In [22]:
df = df.explode('language_name')

In [23]:
projects_by_language = df['language_name'].value_counts()

In [28]:
non_language_programming = ['Makefile', 'Dockerfile', 'Jupyter Notebook', 'Batchfile', 'Procfile', 'Vim Script', 'Nix', 'GLSL', 'Emacs Lisp', 'Roff', 'NSIS', 'AutoHotkey', 'Gnuplot', 'Logos', 'Markdown', 'Lex', 'NASL', 'Rich Text Format', 'TeX', 'Racket', 'XS', 'Bicep', 'AppleScript', 'VBA', 'ASP.NET', 'CodeQL', 'Cap\'n Proto', 'ShaderLab', 'HLSL', 'Rebol', 'mcfunction', 'G-code', 'VHDL', 'SQL', 'AWK', 'PLpgSQL', 'ReScript', 'MDX', 'Verilog', 'POV-Ray SDL', 'Jasmin', 'Cypher', 'StringTemplate', 'POV-Ray SDL', 'WebAssembly', 'Portugol', 'RPC', 'AngelScript', 'ASN.1', 'POV-Ray SDL', 'Latte', 'Stan', 'Cypher Query Language', 'XS', 'Starlark']

In [29]:
filtered_df = df[~df['language_name'].apply(lambda x: any(keyword in x for keyword in non_language_programming))]

# Perform analysis on the filtered dataframe
# For example, count the occurrences of each programming language
language_counts = filtered_df['language_name'].explode().value_counts()

# Print the language counts
print(language_counts)


language_name
Python                      4291
JavaScript                  3487
Shell                       3045
HTML                        2429
TypeScript                  2146
                            ... 
Sieve                          1
MLIR                           1
DIGITAL Command Language       1
Objective-J                    1
sed                            1
Name: count, Length: 184, dtype: int64


In [171]:
import plotly.express as px

# Sort the language counts in descending order
sorted_language_counts = language_counts.sort_values(ascending=False)

# Select the top 20 languages
top_20_languages = sorted_language_counts.head(20)

# Create a bar chart using Plotly
fig = px.bar(x=top_20_languages.index, y=top_20_languages.values)
fig.update_layout(
    xaxis_title='Programming Language',
    yaxis_title='Number of Occurrences',
    title='Top 20 Programming Languages by Occurrences (Excluding Non-language Programming)',
    xaxis_tickangle=-45
)
fig.show()


### relations

In [11]:
# Choose a project for comparison (e.g., "progfolio/elpaca")
chosen_project = "progfolio/elpaca"

# Get the index of the chosen project
chosen_project_index = df[df['full_name'] == chosen_project].index[0]

# Calculate cosine similarity scores for the chosen project
cosine_similarities = cosine_similarity(tfidf_matrix[chosen_project_index], tfidf_matrix).flatten()

# Sort projects based on similarity scores
similar_projects_indices = cosine_similarities.argsort()[::-1][1:]  # Exclude the chosen project itself

# Get top similar projects (e.g., top 5)
top_k = 5
top_similar_projects = df.loc[similar_projects_indices[:top_k], 'full_name']

# Print the top similar projects
print(f"Top {top_k} similar projects to {chosen_project}:")
for i, project in enumerate(top_similar_projects, start=1):
    print(f"{i}. {project}")


Top 5 similar projects to progfolio/elpaca:
1. emacs-openai/openai
2. b4b4r07/afx
3. deinsoftware/swpm
4. ggerganov/whisper.spm
5. Madh93/tpm
